# 0. Introducción 

![](images/mosdef_logo_light.svg)

*MoSDeF* es un proyecto colaborativo, bajo el cargo de Vanderbilt University, que desarrolla una suite de softwares, de código abierto, que busca ayudar en la formación de sistemas químico-biológicos para su simulación molecular. El framework de *MoSDeF* busca ser no específico, esto quiere decir que:

- No tiene preferencias de campo de fuerzas y
- No tiene preferencias de motor

Estos principios permiten la simulación de los sistemas en un gran número de condiciones.

La suite de *MoSDeF* está conformada por tres librerías: `mbuild`, `foyer` y `GMSO`. Las cuales respectivamente se encargan de construir, aplicar campos de fuerzas y guardar el sistema parametrizado.

<center><img src="images/mosdef_scheme.jpg" width="675"/></center>

Puede encontrar más información sobre la utilización de estas librerías en:

- https://mbuild.mosdef.org/
- https://foyer.mosdef.org/
- https://gmso.mosdef.org
- https://github.com/mosdef-hub/CECAM-MoSDeF-Workshop/
- https://github.com/mosdef-hub/mosdef_tutorials (en proceso de actualización)

# 1. Fundamentos de mbuild

`mbuild` utiliza partones compuestos para la creación y diseño de sistemas moleculares complejos. Estos patrones son jerárquicos, como se muestra en la figura,

<center>
    <img src="images/hierarchical_design_image.png"/>
</center>

Cada uno de los componentes en la jerarquía tienen una estructura de datos en común (la clase `mb.Compound`) y estos, a su vez, están compuestos por átomos, a los que les corresponde la clase `mb.Particles`.  

Veamos cómo podemos construir este ejemplo en `mbuild`:

In [20]:
import warnings
warnings.filterwarnings("ignore")
import mbuild as mb
from mbuild.lib.recipes import Alkane
from mbuild.lib.moieties import Silane, CH2
from mbuild.lib.surfaces import Betacristobalite
from mbuild.lib.atoms import H
from mbuild.lib.recipes import Monolayer

In [3]:
CH2().visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [7]:
mb.load("[CH3]", smiles=True).visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [7]:
Alkane(5, cap_end=False).visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [10]:
Silane().visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [21]:
class AlkylSilane(mb.Compound):
    def __init__(self, chain_length):
        super(AlkylSilane, self).__init__()

        alkane = Alkane(chain_length, cap_end=False)
        self.add(alkane, 'alkane')
        silane = Silane()
        self.add(silane, 'silane')
        mb.force_overlap(self['alkane'], self['alkane']['down'], self['silane']['up'])

        self.add(silane['down'], 'down', containment=False)

AlkylSilane(5).visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [2]:
Betacristobalite().visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [5]:
surface = Betacristobalite()
alkylsilane = AlkylSilane(chain_length=10)
hydrogen = H()

monolayer = Monolayer(fractions=[1.0], chains=alkylsilane, backfill=hydrogen,
                      pattern=mb.Grid2DPattern(n=8, m=8),
                      surface=surface, tile_x=2, tile_y=2)
monolayer.visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [56]:
monolayer.save("monolayer.mol2")

In [57]:
mb.load("monolayer.mol2").visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

## 1.1 Construcción de una molécula sencilla 

En esta sección, mostraremos los pasos a seguir para la modelación de la molécula del agua (H2O).

Empezamos importando las librerías necesarias, que en este caso solo será mbuild:

In [8]:
import mbuild as mb

La clase más importante dentro de mbuild es [`Compound`](https://mbuild.mosdef.org/en/stable/topic_guides/data_structures.html#compound), aquí vivirá todo tu sistema molecular. Además, todas las subdivisiones de dicho sistema también serán de esta clase. Seguimos, entonces, nombrando a nuestro compuesto:

In [9]:
h2o = mb.Compound()

El siguiente paso importante, es agregar nuestro átomos. Para esto, hacemos uso de la clase `Particle`. `Particle` es el nivel más bajo de la jerarquía, ya que se refiere a los átomos individualmente. Hay dos variables que se necestian especificar en este caso: el nombre y la posición: 

In [10]:
O = mb.Particle(name="O", pos=[0.0, 0.0, 0.0])
H1 = mb.Particle(name="H", pos=[0.1, 0.0, 0.0])
H2 = mb.Particle(name="H", pos=[-0.1, 0.0, 0.0])

Ahora, necesitamos agregar estos átomos a la jerarquía de nuestro compuesto. Para esto, utilizamos el método `add` de `Compound` con el argumento `new_child` especificando en los elementos a añadir: 

In [11]:
h2o.add(new_child=[O, H1, H2])

Veamos lo que hemos construido utilizando el método `visualize()`:

In [16]:
h2o.visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

También, de manera más compacta, podemos ver las divisiones utilizando el atributo `children`, el cual nos permite ver los componenntes un nivel abajo en la jerarquía:

In [17]:
h2o.children

[<O pos=([0. 0. 0.]), 0 bonds, id: 127722604917376>,
 <H pos=([0.1 0.  0. ]), 0 bonds, id: 127722604920736>,
 <H pos=([-0.1  0.   0. ]), 0 bonds, id: 127722604917232>]

O el método `particles()` el cual nos permite ver el nivel más elemental de esta:

In [18]:
list(h2o.particles())

[<O pos=([0. 0. 0.]), 0 bonds, id: 127722604917376>,
 <H pos=([0.1 0.  0. ]), 0 bonds, id: 127722604920736>,
 <H pos=([-0.1  0.   0. ]), 0 bonds, id: 127722604917232>]

En este caso en particular, solamente hacemos uso de dos niveles, por lo que ambos regresan lo mismo. No obstante, esto no sucede en compuestos más grandes.

Como útlimo paso, necesitamos crear los enlaces entre los átomos. Esto se consigue usando el método `add_bond()`:

In [24]:
h2o.add_bond((O, H1))
h2o.add_bond((O, H2))
h2o.visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

Para trabajos posteriores, es importante guardar nuestro progreso. Esto lo hacemos con el método `save()`:

In [38]:
h2o.save("h2o.mol2", overwrite=True)

**Nota**: guardar a .pdb no sirve, no guarda los enlaces. Use *Open Babel* si requiere transformar el tipo de archivo:

```
obabel file.mol2 -O file.pdb
```

Muy probablemente *Open Babel* ya se encuentre en su dispositivo, por lo que no tiene que instalar nada adicional.

Una manera de acelerar el proceso de crear moléculas, es a partir de generar clases que hereden `mb.Compound`:

In [62]:
class H2O(mb.Compound):
    def __init__(self):
        super(H2O, self).__init__()
    
        O = mb.Particle(name="O", pos=[0.0, 0.0, 0.0])
        H1 = mb.Particle(name="H", pos=[0.1, 0.0, 0.0])
        H2 = mb.Particle(name="H", pos=[-0.1, 0.0, 0.0])
        self.add(new_child=[O, H1, H2])
        self.add_bond((O, H1))
        self.add_bond((O, H2))
        self.visualize()

H2O().visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

## 1.2 Puertos

Acabamos de ver que podemos utilizar `.add_bond()` para crear enlaces entre los átomos. No obstante, los enlaces se haría independientemente de la posición de las partículas. Miremos como ejemplo el siguiente sistema.

In [2]:
import mbuild as mb

ch2 = mb.Compound()
carbon = mb.Particle(pos=[0.0, 0.0, 0.0], name='C')
hydrogen = mb.Particle(pos=[1.0, 0.0, 0.0], name='H')
hydrogen2 = mb.Particle(pos=[2.0, 0.0, 0.0], name='H')
ch2.add([carbon, hydrogen, hydrogen2])
ch2.visualize()

/home/p-pomares/anaconda3/lib/python3.11/site-packages/mdtraj/formats/__init__.py:6: DeprecationWarning: 'xdrlib' is deprecated and slated for removal in Python 3.13
  from .xtc import XTCTrajectoryFile
/home/p-pomares/anaconda3/lib/python3.11/site-packages/lark/utils.py:163: DeprecationWarning: module 'sre_parse' is deprecated
  import sre_parse
/home/p-pomares/anaconda3/lib/python3.11/site-packages/lark/utils.py:164: DeprecationWarning: module 'sre_constants' is deprecated
  import sre_constants
/home/p-pomares/anaconda3/lib/python3.11/site-packages/mbuild/recipes/__init__.py:13: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  entry_points = metadata.entry_points()["mbuild.plugins"]


You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Observemos qué pasa si simplemente usamos `add_bond()`:

In [7]:
ch2.add_bond([carbon, hydrogen])
ch2.add_bond([carbon, hydrogen2])
ch2.visualize()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Es por eso que en `mbuild` existe el objeto llamado `Port`. Se puede pensar de los `Ports` como enlaces incompletos que, al asignarle otro, se acompleta manteniendo la geometría. Un puerto se crea de la siguiente manera:

In [10]:
ch2 = mb.Compound()
carbon = mb.Particle(pos=[0.0, 0.0, 0.0], name='C')
hydrogen = mb.Particle(pos=[1.0, 0.0, 0.0], name='H')
hydrogen2 = mb.Particle(pos=[2.0, 0.0, 0.0], name='H')
ch2.add([carbon, hydrogen, hydrogen2])
ch2.visualize()

port_C = mb.Port(anchor=carbon, orientation=[1, 0, 0], separation=0.05)
port_C

<Port, anchor: 'C', labels: , id: 133847536333136>

Como se puede observar, el "anchor" es la partícula a la cual se le asigna ese puerto en específico, junto con una orientación y una separación, que va ser útil para conservar la longitud de los enlaces. Creemos los puertos restantes,

In [11]:
port2_C = mb.Port(anchor=carbon, orientation=[-1, 0, 0], separation=0.05)
port_H = mb.Port(anchor=hydrogen, orientation=[1, 0, 0], separation=0.05)
port2_H = mb.Port(anchor=hydrogen2, orientation=[1, 0, 0], separation=0.05)

Se tiene que especificar que se le agrega a la partícula. Esto se hace con:

In [12]:
ch2.add(port_C, label='right')
ch2.add(port2_C, label='left')
ch2.add(port_H, label='H1')
ch2.add(port2_H, label='H2')
ch2['right']

<Port, anchor: 'C', labels: ['right'], id: 133847536333136>

In [13]:
ch2.visualize(show_ports=True)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Lo que ahora falta hacer es "completar" los enlaces a través de la función `force_overlap()`. Especificando cual puerto se mueve a cual otro:

In [14]:
mb.force_overlap(move_this=hydrogen,
                 from_positions=ch2['H1'],
                 to_positions=ch2['right'])

mb.force_overlap(move_this=hydrogen2,
                 from_positions=ch2['H2'],
                 to_positions=ch2['left'])

ch2.visualize(show_ports=True)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Así como creamos el enlace, podemos destruirlos usando `remove_bond()`:

In [15]:
ch2.remove_bond(particle_pair=(carbon, hydrogen))
ch2.visualize(show_ports=True)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Es importante notar, que cuando usamos `remove_bond` eliminamos enlace y añadimos unos puertos nuevos en su lugar, por lo que estos no van a conservar el nombre que se les asignó originalmente. Podemos ver cuáles partículas y puertos hay disponibles usando `available_ports()`:

In [16]:
ch2.available_ports()

[<Port, anchor: 'C', labels: ['port[0]'], id: 133849486623120>,
 <Port, anchor: 'H', labels: ['port[1]'], id: 133847824506448>]

## 1.3 Construcción de moléculas más complejas

Con el conocimiento que hemos adquirido hasta ahora, podemos empezar con una construcción más avanzada. Primero, definamos unas clases: 

In [4]:
import mbuild as mb

class Hydrogen(mb.Compound):
    def __init__(self):
        super(Hydrogen, self).__init__()
        
        self.add(mb.Particle(name='H'))
        up_port = mb.Port(anchor=self[0], orientation=[0, 0, 1], separation=0.05)
        self.add(up_port, 'up')

class CH2(mb.Compound):
    def __init__(self):
        super(CH2, self).__init__()

        mb.load('utils/ch2.pdb', compound=self)
        carbon = list(self.particles_by_name('C'))[0]
        up_port = mb.Port(anchor=carbon, orientation=[0, 0, 1], separation=0.075)
        down_port = mb.Port(anchor=carbon, orientation=[0, 0, -1], separation=0.075)
        self.add(up_port, label='up')
        self.add(down_port, label='down')

In [13]:
CH2().visualize(show_ports=True)

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Con estos ingredientes podemos crear cualquier alcano. Por ejemplo, veamos cómo podmeos construir un pentano. Como bien sabemos, un pentano está compuesto por 5 átomo de carbono. Empecemos definiendo nuestro compuesto, 

In [73]:
pentane = mb.Compound()

Ahora, agreguemos una molécula de CH2 y agreguémosle un hidrógeno, esto nos servirá de base para construir el resto el pentano. Podemos agregar el resto de los carbonos uno por uno, pero sería más sencillo usar un ciclo `for`: 

In [74]:
last_unit = CH2()
h1 = Hydrogen()
mb.force_overlap(move_this=h1,
                 from_positions=h1['up'],
                 to_positions=last_unit['up'])
pentane.add(h1, label='up-cap')
pentane.add(last_unit, label='ch2[$]')

for i in range(4):
    current_unit = CH2()
    mb.force_overlap(move_this=current_unit,
                     from_positions=current_unit['up'],
                     to_positions=last_unit['down'])
    pentane.add(current_unit, label='ch2[$]')
    last_unit=current_unit

pentane.visualize(show_ports=True)

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

Solo falta agregar un hidrógeno en la tapa superior:

In [75]:
h2 = Hydrogen()

mb.force_overlap(move_this=h2,
                 from_positions=h2['up'],
                 to_positions=last_unit['down'])
pentane.add(h2, label='down-cap')

In [72]:
pentane.visualize(show_ports=True)

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

Todo esto lo podemos concentrar, por supuesto, en una sola clase como ya lo hemos visto anteriormente:

In [79]:
class Pentane(mb.Compound):
    def __init__(self):
        super(Pentane, self).__init__()

        last_unit = CH2()
        h1 = Hydrogen()
        h2 = Hydrogen()
        mb.force_overlap(move_this=h1,
                         from_positions=h1['up'],
                         to_positions=last_unit['up'])
        self.add(h1, label='up-cap')
        self.add(last_unit, label='ch2[$]')
        
        for i in range(4):
            current_unit = CH2()
            mb.force_overlap(move_this=current_unit,
                             from_positions=current_unit['up'],
                             to_positions=last_unit['down'])
            self.add(current_unit, label='ch2[$]')
            last_unit=current_unit
        
        mb.force_overlap(move_this=h2,
                         from_positions=h2['up'],
                         to_positions=last_unit['down'])
        self.add(h2, label='down-cap')

Pentane().visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

No obstante, sería molesto tener que crear una nueva clase para cada alcano que se use, por lo que sería más fácil crear una clase flexible la cual nos pueda regresar una molécula de longitud arbitraria. 

Esto es muy sencillo, únicamente hace falta modificar ligeramente la última clase que se mostró, `Pentane`, incluyendo un parámetro que nos indique la longitud deseada:

In [7]:
class Alkane(mb.Compound):
    def __init__(self, length):
        super(Alkane, self).__init__()

        last_unit = CH2()
        h1 = Hydrogen()
        h2 = Hydrogen()
        mb.force_overlap(move_this=h1,
                         from_positions=h1['up'],
                         to_positions=last_unit['up'])
        self.add(last_unit, label='ch2[$]')
        self.add(h1, label='up-cap')
        
        for i in range(length - 1):
            current_unit = CH2()
            mb.force_overlap(move_this=current_unit,
                             from_positions=current_unit['up'],
                             to_positions=last_unit['down'])
            self.add(current_unit, label='ch2[$]')
            last_unit=current_unit
        
        mb.force_overlap(move_this=h2,
                         from_positions=h2['up'],
                         to_positions=last_unit['down'])
        self.add(h2, label='down-cap')

Alkane(length=10).visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

Esta función la podemos encontrar en `mbuild` por default en `mbuild.lib.recipes.Alkane()` y se usa de la siguiente manera:

In [11]:
from mbuild.lib.recipes import Alkane

hexane = Alkane(6)
hexane.visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

## 1.4 Minimización de Energía

Lo que hemos visto hasta ahora para la construcción molecular ha sido útil, no obstante podemos observar que no es particularmente realista. Todos los átomos parecen estar sobre el mismo plano, los ángulos de los enlaces son rectos, etc. Mientras que durante la construcción podríamos ser más meticulosos ingresando manualmente los parámetros correctos, es más sencillo aplicarle un campo de fuerza para que llegue la molécula a una forma más correcta.

Aunque anteriormente se había mencionado que es `foyer` quien se encarga de los campos de fuerza, existen funciones dentro de `mbuild` que aplican dichos campos a compuestos relativamente sencillos. Esto se logra usando la función `energy_minimize()` de la clase `Compound`:

In [1]:
import mbuild as mb
from mbuild.lib.recipes import Alkane

help(mb.Compound.energy_minimize)

/home/p-pomares/anaconda3/envs/tutorial_mosdef/lib/python3.10/site-packages/mdtraj/geometry/order.py:25: DeprecationWarning: pkg_resources is deprecated as an API. See https://setuptools.pypa.io/en/latest/pkg_resources.html
  from pkg_resources import parse_version
/home/p-pomares/anaconda3/envs/tutorial_mosdef/lib/python3.10/site-packages/pkg_resources/__init__.py:2832: DeprecationWarning: Deprecated call to `pkg_resources.declare_namespace('google')`.
Implementing implicit namespace packages (as specified in PEP 420) is preferred to `pkg_resources.declare_namespace`. See https://setuptools.pypa.io/en/latest/references/keywords.html#keyword-namespace-packages
  declare_namespace(pkg)


Help on function energy_minimize in module mbuild.compound:

energy_minimize(self, forcefield='UFF', steps=1000, shift_com=True, anchor=None, **kwargs)
    Perform an energy minimization on a Compound.
    
    Default behavior utilizes `Open Babel <http://openbabel.org/docs/dev/>`_
    to perform an energy minimization/geometry optimization on a Compound by
    applying a generic force field
    
    Can also utilize `OpenMM <http://openmm.org/>`_ to energy minimize after
    atomtyping a Compound using
    `Foyer <https://github.com/mosdef-hub/foyer>`_ to apply a forcefield XML
    file that contains valid SMARTS strings.
    
    This function is primarily intended to be used on smaller components,
    with sizes on the order of 10's to 100's of particles, as the energy
    minimization scales poorly with the number of particles.
    
    Parameters
    ----------
    steps : int, optional, default=1000
        The number of optimization iterations
    forcefield : str, optional, de

/home/p-pomares/anaconda3/envs/tutorial_mosdef/lib/python3.10/site-packages/mbuild/recipes/__init__.py:13: DeprecationWarning: SelectableGroups dict interface is deprecated. Use select.
  entry_points = metadata.entry_points()["mbuild.plugins"]


Observemos como actúa si le aplicamos la minimización de energía a un alcano que se construyó usando la clase que creamos con anterioridad:

In [2]:
hexane = Alkane(6)
hexane.energy_minimize()
hexane.visualize(backend='NGLView')

/home/p-pomares/anaconda3/envs/tutorial_mosdef/lib/python3.10/site-packages/mbuild/compound.py:2888: UserWarning: Performing energy minimization using the Open Babel package. Please refer to the documentation to find the appropriate citations for Open Babel and the UFF force field
  warn(


NGLWidget()

Los principales parámetros que se pueden modificar son los `steps` (que por default están en 1000) y el campo de fuerza, `forcefield`, que es UFF por default. Igual se pueden usar: GAFF, Ghemical, MMFF94 o MMF94s a través de Openbabel o se puede usar algún archivo XML  a través de OpenMM.

In [22]:
hexane = Alkane(6)
hexane.energy_minimize(steps=4000, forcefield="GAFF", algorithm="steep")
hexane.visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

Para más detalles de la utilización de esta función recomiendo checar el siguiente repositorio de github: https://github.com/chrisiacovella/mbuild_energy_minimization

## 1.5 Construcción de Polímeros

Como se podrán imaginar, el proceso llevado a cabo con los alcanos puede ser generalizado para cualquier tipo de molécula. Para simplificar este proceso se usa la clase `mb.Polymer`. Esta clase toma dos, o más, monómeros y los une en secuencia que especificamos.  

In [38]:
import mbuild as mb
from mbuild.lib.recipes.polymer import Polymer

help(Polymer)

Help on class Polymer in module mbuild.lib.recipes.polymer:

class Polymer(mbuild.compound.Compound)
 |  Polymer(monomers=None, end_groups=None)
 |  
 |  Connect one or more components in a specified sequence.
 |  
 |  Attributes
 |  ----------
 |  monomers : list of mbuild.Compounds
 |      The compound(s) to replicate. Add to this list using the add_monomers
 |      method.
 |  end_groups : list of mbuild.Compounds
 |      The compound to cap the end of the polymer. Add to this list using the
 |      add_end_groups method.
 |  
 |  Methods
 |  -------
 |  add_monomer(monomer, indices, separation, port_labels, orientation, replace)
 |      Use to add a monomer compound to Polymer.monomers
 |  
 |  add_end_groups(compound, index, separation, orientation, replace)
 |      Use to add an end group compound to Polymer.end_groups
 |  
 |  build(n, sequence)
 |      Use to create a single polymer compound. This method uses the compounds
 |      created by calling the add_monomer and add_end_

Generemos un polímero simple para ejemplificar una manera de usar esta clase. Primero, hagamos unas moléculas que usaremos para el ejemplo.

In [13]:
class CH2(mb.Compound):
    def __init__(self):
        super(CH2, self).__init__()
        
        mb.load('utils/ch2.pdb', compound=self)
        carbon = list(self.particles_by_name('C'))[0]
        up_port = mb.Port(anchor=carbon, orientation=[0, 0, 1], separation=0.075)
        down_port = mb.Port(anchor=carbon, orientation=[0, 0, -1], separation=0.075)
        self.add(up_port, label='up')
        self.add(down_port, label='down')

class O(mb.Compound):
    def __init__(self):
        super(O, self).__init__()
        
        self.add(mb.Particle(name='O'))
        up_port = mb.Port(anchor=self[0], orientation=[0, 0, 1], separation=0.075)
        self.add(up_port, 'up')
        down_port = mb.Port(anchor=self[0], orientation=[0, 0, -1], separation=0.075)
        self.add(down_port, 'down')

class CF2(mb.Compound):
    def __init__(self):
        super(CF2, self).__init__()
        
        mb.load('utils/cf2.pdb', compound=self)
        carbon = list(self.particles_by_name('C'))[0]
        up_port = mb.Port(anchor=carbon, orientation=[0, 0, 1], separation=0.075)
        down_port = mb.Port(anchor=carbon, orientation=[0, 0, -1], separation=0.075)
        self.add(up_port, label='up')
        self.add(down_port, label='down')

Primero, tenemos que asignarle la clase `Polymer` a alguna variable y poniéndole como argumento los monómeros que queremos agregar. Después, se le tiene que aplicar a la variable la función `build`, con los argumentos `n`, que corresponde al número de repeticiones que se hará la secuencia, y `sequence`, el cual es la secuencia que seguirán los monómeros. Los monómeros serán representados con una letra mayúscula de acuerdo a su orden. (La primero será A, la segunda B, etc.)

In [6]:
poli = Polymer(monomers=[CH2(), O()])
poli.build(n=2, sequence="ABAAB")
poli.visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [12]:
poli = Polymer(monomers=[CH2(), O(), CF2()])
poli.build(n=2, sequence="ABACABCC")
poli.visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

Este método es más útil para construir polímeros rápidamente. No obstante, para crear clases generales de polímeros, es más útil otro sintax un poco más elaboraado. Mostrémoslo con un ejemplo: un alcano semifluorado.

Empecemos elaborando el polímero de la manera anterior para visualizarlo: 

In [15]:
semifluorinated_hexane = Polymer(monomers=(CH2(), CF2()))
semifluorinated_hexane.build(sequence='AAABBB', n=1)
semifluorinated_hexane.visualize(backend="NGLView")

NGLWidget()

Podemos observar que podemos dividr el ASF en dos secciones: un alcano y un polifluroalquilo (PFA). Podemos primero hacer un polímero de esos componentes y después juntarlos en uno más grande.

In [26]:
class CF2(mb.Compound):
    def __init__(self):
        super(CF2, self).__init__()
        
        mb.load('utils/cf2.pdb', compound=self)
        carbon = list(self.particles_by_name('C'))[0]
        fluorine = mb.Particle(pos=[0.0, 0.0, 0.1], name='F')
        fluorine2 = mb.Particle(pos=[0.0, 0.0, -0.1], name='F')
        self.add([fluorine, fluorine2])
        self.add_bond((carbon, fluorine))
        self.add_bond((carbon, fluorine2))

class CH2(mb.Compound):
    def __init__(self):
        super(CH2, self).__init__()
        
        mb.load('utils/ch2.pdb', compound=self)
        carbon = list(self.particles_by_name('C'))[0]
        hydrogen = mb.Particle(pos=[0.0, 0.0, 0.1], name='H')
        hydrogen2 = mb.Particle(pos=[0.0, 0.0, -0.1], name='H')
        self.add([hydrogen, hydrogen2])
        self.add_bond((carbon, hydrogen))
        self.add_bond((carbon, hydrogen2))

ch2 = mb.load("C", smiles=True)

CF2().visualize(show_ports=True, backend="NGLview")

NGLWidget()

Esto lo hacemos definiendo primero nuestro polímeros, solo que en esta ocasión no metemos argumentos:

In [27]:
alkane_block = Polymer()
pfa_block = Polymer()

Después, se tiene que hacer uso de la función `add_monomer`:, y se contruye como se hizo en el otro método:

In [28]:
alkane_block.add_monomer(CH2(), indices=[3, 4], replace=True)
alkane_block.build(n=3)

pfa_block = Polymer()
pfa_block.add_monomer(CF2(), indices=[3, 4], replace=True)
pfa_block.build(n=3)

Los índices en este caso corresponden a los átomos que serán reemplazados. Depués, podemos juntar estos polímeros en un alcano semifluorado:

In [29]:
semifluorinated_hexane = Polymer()
semifluorinated_hexane.add_monomer(
    alkane_block,
    indices=[-2, -1],
    replace=True
)
semifluorinated_hexane.add_monomer(
    pfa_block,
    indices=[-2, -1],
    replace=True
)
semifluorinated_hexane.build(sequence='AB', n=1)

semifluorinated_hexane.visualize(backend="NGLView")

NGLWidget()

Todo esto lo podemos condensar en una sola función general:

In [32]:

class Semifluorinated(mb.Compound):
    def __init__(self, alkane_length, pfa_length):
        super(Semifluorinated, self).__init__()
        
        alkane_block = Polymer()
        alkane_block.add_monomer(CH2(), indices=[3, 4], replace=True)
        alkane_block.build(n=alkane_length)
        
        pfa_block = Polymer()
        pfa_block.add_monomer(CF2(), indices=[3, 4], replace=True)
        pfa_block.build(n=pfa_length)
        semifluorinated_hexane = Polymer()
        semifluorinated_hexane.add_monomer(
            alkane_block,
            indices=[-2, -1],
            replace=True
        )
        semifluorinated_hexane.add_monomer(
            pfa_block,
            indices=[-2, -1],
            replace=True
        )
        semifluorinated_hexane.build(sequence='AB', n=1)

        self.add(semifluorinated_hexane)

semifluorinated_alkane = Semifluorinated(alkane_length=3, pfa_length=3)
semifluorinated_alkane.visualize(backend="NGLView")

NGLWidget()

## 1.6 Creación de Sistemas con varias moléculas

Es bastante común que cuando uno trabaje en simulación molecular uno lo aplique a sistemas con un gran número de moléculas, por lo que en esta sección se hablará de cómo pueden establercerse. 

Empecemos observando cómo podemos crear patrones de moléculas, por simplicitud, alcanos. Esto se puede hacer de dos maneras, manulamente y usando funciones de MoSDeF, nos fijaremos primero en el proceso manual. Para comenzar, agreguemos un hexano y el compuesto donde se encontrarán las moléculas: 

In [21]:
import mbuild as mb
from mbuild.lib.recipes import Alkane

box_hexane = mb.Compound()
hexane = Alkane(6)

Lo podemos trasladar el hexano al origen usando la fuanción `translate` y creando un arreglo $3\times 3\times 3$ a través de un loop:

In [22]:
hexane.translate(-hexane.center)

for i in range(0,3):
    for j in range(0,3):
        for k in range(0,3):
            temp_hexane = mb.clone(hexane)
            pos = [i, j, k]
            temp_hexane.translate_to(pos)
            box_hexane.add(temp_hexane)

box_hexane.visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

Pero como también se mencionó, se pueden usar funciones de MoSDeF para obtener el mismo resultado. En este caso `Grid3DPattern`:

In [27]:
box_hexane = mb.Compound()

grid3d = mb.Grid3DPattern(3, 3, 3)

# Podemos escalar el patrón para que sea más grande usando
grid3d.scale(3.0)

for position in grid3d:
    temp_hexane = mb.clone(hexane)
    temp_hexane.translate_to(position)
    box_hexane.add(temp_hexane)

box_hexane.visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

Otra función que vale la pena mencionar es `spin`, el cual, como se podrán imaginar, gira las moléculas:

In [34]:
box_hexane = mb.Compound()

grid3d = mb.Grid3DPattern(2, 1, 2)

grid3d.scale(2.0)
for position in grid3d:
    temp_hexane = mb.clone(hexane)
    temp_hexane.spin(0.5, around=[1,0,0])
    temp_hexane.translate_to(position)
    box_hexane.add(temp_hexane)

box_hexane.visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

Esto se puede usar con `Random`, por supuesto:

In [33]:
import random
from numpy import pi
box_hexane = mb.Compound()

grid3d = mb.Grid3DPattern(4, 1, 4)

rnd = random.Random()
    
grid3d.scale(5.0)
for position in grid3d:
    temp_hexane = mb.clone(hexane)
    # una rotación por eje
    temp_hexane.spin(rnd.uniform(0, 2 * pi), around=[1,0,0])
    temp_hexane.spin(rnd.uniform(0, 2 * pi), around=[0,1,0])
    temp_hexane.spin(rnd.uniform(0, 2 * pi), around=[0,0,1])
    temp_hexane.translate_to(position)
    box_hexane.add(temp_hexane)

box_hexane.visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

### 1.6.1 Box

Otra manera bastante práctica de crear sistemas grandes es a través de la clase `mb.Box` y la función `fill_box`. 

Como podrán intuir, tenemos que crear una variable de clase `Box` y como argumento tenemos que definir sus dimensiones:

In [35]:
box = mb.Box(lengths=[5, 5, 5])

Ahora, con la función `fill_box` llenamos la caja de algún otro compuesto. Esto se tiene que especificar con el argumento `compound`, así como de `n_compound` que indica cuantos compuestos se añadirán:

In [36]:
box_hexane = mb.fill_box(compound=hexane, n_compounds=10, box=box)
box_hexane.visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

En `compound` podemos agregar un listado de compuestos que queremos agregar, pero el `n_compound` también deberá serlo.

In [40]:
class CF2(mb.Compound):
    def __init__(self):
        super(CF2, self).__init__()
        
        mb.load('utils/cf2.pdb', compound=self)
        carbon = list(self.particles_by_name('C'))[0]
        fluorine = mb.Particle(pos=[0.0, 0.0, 0.1], name='F')
        fluorine2 = mb.Particle(pos=[0.0, 0.0, -0.1], name='F')
        self.add([fluorine, fluorine2])
        self.add_bond((carbon, fluorine))
        self.add_bond((carbon, fluorine2))

pfa_block = Polymer()
pfa_block.add_monomer(CF2(), indices=[3, 4], replace=True)
pfa_block.build(n=6)

In [42]:
box_poly = mb.fill_box(compound=[hexane, pfa_block], n_compounds=[10, 10], box=box)
box_poly.visualize()

3Dmol.js failed to load for some reason. Please check your browser console for error messages.

# 2. Foyer 

Por simplicidad, no nos adentraremos mucho en las explicaciones del uso de `Foyer`, pero sí mostraremos usos básicos de este. Como se mencionó al principio del curso, `Foyer` es quien se encarga de aplicar campos de fuerza, pero para eso necesitamos tener disponible